<table style="width: 100%; border-style: none">
<tr style="border-style: none; background-color: #82a8cf">
<td style="border-style: none; width: 1%; text-align: left; font-size: 18px; color: #ffffff">Institut f&uuml;r Theoretische Physik<br /> <font color="#e6e6e6">Universit&auml;t zu K&ouml;ln </font></td>
<td style="border-style: none; width: 1%; font-size: 16px">&nbsp;</td>
<td style="border-style: none; width: 1%; text-align: right; font-size: 18px; color: #ffffff">Prof. Dr. Simon Trebst<br /> <font color="#e6e6e6"> Christoph Berke </font> </td>
</tr>
</table>
<hr  style="height: 2px; border-color: #606060; background-color: #606060"> 
<h1 style="font-weight:200; text-align: center; margin: 0px; font-size: 48px; padding:0px; color: #606060">Statistische Physik </h1>
<h1 style="font-weight:light; text-align: center; margin: 10px; padding:0px; color: #606060">&Uuml;bungsblatt 3</h1>
<hr  style="height: 2px; border-color: #606060; background-color: #606060"> 
<h3 style="font-weight:400; text-align: center; margin: 0px; font-size: 20px; padding:0px; margin-bottom: 20px; color: #606060">Wintersemester 23/24</h3>


<font size="4" color="#606060">**Website:** <a href="https://www.thp.uni-koeln.de/trebst/Lectures/2023-StatPhys.shtml" style="color:#82a8cf; text-decoration: underline;text-decoration-style: dotted;">https://www.thp.uni-koeln.de/trebst/Lectures/2023-StatPhys.shtml</a></font>

<font size="4" color="#606060">**Abgabe**: <span style="color:#82a8cf"> 30.10.2023, 10:00 Uhr </span> <span style="float:right;">**Besprechung**: 31.10.2023 </span></font>

<font size="4" color="#606060">**Name**: <span style="color:#82a8cf"> Bitte geben Sie Ihren Namen an.  </span> </font>

<table style="border-style: none; width: 100%; background-color: #FFFFFF"><tr style="border-style: none;">
<td style="border-style: none; width:2%; text-align: left; font-size: 25px; font-weight: 200;background-color: #FFFFFF">Aufgabe 12: Satz von Liouville </td>
<td style="border-style: none; width: 1%; text-align: right; font-size: 15px;background-color: #FFFFFF">[8 + 2 Punkte, davon 4 Punkte für Teil b)]</td></tr></table>

### b) ### 
Mit Hilfe dieses Notebooks können Sie die Phasenraumdynamik unterschiedlicher physikalischer Systeme untersuchen. Genauer wollen wir die zeitliche Entwicklung eines *Phasenraumvolumens* nachvollziehen. In den ersten Zellen werden zunächst einige Funktionen bereit gestellt, die die gewünschten Anfangsbedingungen erzeugen und die die zu lösende Differentialgleichungssysteme integrieren. Sie können diese Funktionen unverändert übernehmen. Lesen Sie sich die nachfolgenden Zellen trotzdem aufmerksam durch, und ergänzen Sie anschließend weiter unten, an den markierten Stellen, Ihren Code, um die auf dem Aufgabenblatt gegebenen Systeme zu implementieren.

#### Einbinden der benötigten Pakete ####

In [ ]:
using DifferentialEquations, GLMakie

#### Integration der Differentialgleichung um einen Zeitschritt. ####

In [ ]:
# Funktion integriert die Differentialgleichung um den Zeitschritt dt weiter.
# Hierbei ist 
# - integ ein ODEIntegrator (spezieller Datentyp aus dem Paket DifferentialEquations)
# - points eine Observable, die die aktuellen Orte und Impulse speichert.
# - dt der Zeitschritt, den die DGL nach vorne entwickelt wird.
function animstep!(integ, points, dt)
    
    # Differentialgleichung einen Schritt weiter integrieren.
    step!(integ, dt, true)
    
    # Update der Observablen, die die aktuellen Orte/Impulse speichert.
    for i in 1:size(points[], 1)
        points[][i] = Point2f(integ[2*i-1], integ[2*i])
    end
    
    # Observable auf Update aufmerksam machen
    notify(points)
    
end

#### Erzeuge Anfangsbedingungen. ####

In [ ]:
# Erzeuge zufällige Anfangsbedingungen (x,p), die gleichmäßig verteilt innerhalb eines Kreises 
# mit Mittelpunkt (x0,p0) und Radius R liegen. N ist die Anzahl der zurückgegebenen Wertepaare.
function get_init_inner(x0,p0,R,N)

    # generate equally distributed random initial condition in circle.
    r, phi = R * sqrt.(rand(N)), rand(N) * 2 * pi
    x, p = x0 .+ r .* cos.(phi),  p0 .+ r .* sin.(phi)

    # provide correct formatting: [q1,p1,...,qN,pN]
    u0 = zeros(2*N)
    for i in 1:N
        u0[2*i-1] = x[i]
        u0[2*i] = p[i]
    end 
    
    return u0
end

# Erzeuge Anfangsbedingungen (x,p), die gleichmäßig verteilt auf einem Kreis mit Mittel-
# punkt (x0,p0) und Radius R liegen. N ist die Anzahl der zurückgegebenen Wertepaare
function get_init_border(x0,p0,R,N)

    # generate equally distributed initial condition on circle.
    phi = range(0,2*pi, length = N)
    x, p = x0 .+ R .* cos.(phi),  p0 .+ R .* sin.(phi)

    # provide correct formatting: [q1,p1,...,qN,pN]
    u0 = zeros(2*N)
    for i in 1:N
        u0[2*i-1] = x[i]
        u0[2*i] = p[i]
    end 
    
    return u0
end

#### Definiere das DGL Problem. ####

In [ ]:
# Funktion erzeugt zwei ODE Probleme (für das Innere und den Rand des Volumenelements)
# Ninner / Nborder sind die jeweilige Anzahl der Anfangspunkte, R ist der Kreisradius.
# Die Funktion problem definiert das Differentialgleichungsproblem (siehe unten).
function generate_ODEprob(Ninner, Nborder, R, problem::Function)
    
    tspan = (0,10)
    params1, params2 = [Ninner], [Nborder]
  
    u0inner = get_init_inner(0,0,R,Ninner)
    u0border = get_init_border(0,0,R,Nborder)

    prob_inner = ODEProblem(problem, u0inner, tspan, params1)
    prob_border = ODEProblem(problem, u0border, tspan, params2)

    # initialize integrators for two sets of solutions
    integ_inner = init(prob_inner, save_everystep = false);
    integ_border = init(prob_border, save_everystep = false);

    # Observablen zur Darstellung.
    points_inner = [Point2f(u0inner[2*i-1], u0inner[2*i]) for i in 1:Ninner]
    points_border = [Point2f(u0border[2*i-1], u0border[2*i]) for i in 1:Nborder]
    points_inner = Observable(points_inner)
    points_border = Observable(points_border)
    
    return integ_inner, integ_border, points_inner, points_border
end 

### In den folgenden Zellen sind Sie gefragt: ###
Lesen Sie sich die nachfolgende Zelle gründlich durch und vollziehen Sie nach, wie die Bewegungsgleichungen des Systems aus $N$ ungekoppelten, harmonischen Oszillatoren implementiert wurde. Führen Sie anschließend die übernächste Zelle aus und machen Sie sich mit der Simulation vertraut. Sie können per Mausklick ein neues Phasenraumvolument auswählen und die Zeitentwicklung erneut starten. Zoomen ist per Mausrad (oder äquivalenter Funktion) möglich, der sichtbare Bereich lässt sich mit gedrückter rechter Maustaste verschieben.

Ergänzen Sie anschließend - analog zum harmonischen Oszillator - die Differentialgleichungen, die das gedämpfte Pendel und das System mit der auf dem Aufgabenblatt gegebenen Hamiltonfunktion beschreiben. Für das gedämpfte Pendel können Sie $\gamma = 0.1$, $m =1$ und $ K = 3$ setzen.
Visualisieren Sie anschließend auch die Phasenraumdynamik der beiden neuen Systeme und beschreiben Sie Ihre Beobachtungen. 

**Optional:** Implementieren Sie auch die Bewegungsgleichungen des Duffing-Oszillators auf geeignete Weise und untersuchen Sie das System für verschiedene Parametersätze, etwa $\alpha = -1$, $\beta = 1$, $\gamma = 0.02$, $\delta = 3$, $\omega = 1$.

In [ ]:
# Beispiel fuer Implementierung der DGL: 
# Ein einzelner Oszillator.
# du = [dq/dt, dp/dt]
# u = [q,p]
# p = [sonstige Parameter]
# t = Zeit (falls DGL explizit zeitabhängig wäre)
function oscillator(du, u, p, t)
    du[1] =  u[2]
    du[2] = -u[1]
end

# N ungekoppelte Oszillatoren.
# du = [q1,p1,...,qN,pN]
# du = [dq1/dt, dp1/dt, ... , dqN/dt, dpN/dt]
# p = [sonstige Parameter]. Hier: Anzahl der Oszillatoren.
# t = Zeit (falls DGL explizit zeitabhängig wäre)
function Noscillators(du, u, p, t)
    N = p[1]
    for i in 1:2:(2*N-1)
        du[i] = u[i+1]
        du[i+1] = -u[i]
    end
    return
end


function Ndamped_oscillators(du, u, p, t)
    ### Ergänzen Sie hier Ihren Code ###
    return
end

### Ergänzen Sie hier die Bewegungsgleichungen der gegebenen Hamilton-Funktion ###

In [ ]:
# Definiere das DGL Problem:

# Anzahl an Punkten innen und auf Rand, Radius der Anfangsbedingungen.
NI, NB, R = 1000, 1001, 5

# Initialisiere das DGL Problem und die Observablen zur Darstellung der Trajektorien.
IInner, IBorder, PInner, PBorder = generate_ODEprob(NI, NB, R, Noscillators)


########################################################
######### Visualisierung mit Makie #####################
#########(kann unverändert übernommen werden) ########## 
########################################################

fig = Figure()
ax = Axis(fig[1,1])
scatter!(ax, PInner)#, color = xvals, colormap = :viridis)
scatter!(ax, PBorder)#, color = xvals, colormap = :viridis)

# Makie Einstellungen.
limits!(ax, -8,8,-8,8)
hidedecorations!(ax)
Makie.deactivate_interaction!(ax, :rectanglezoom)
spoint = select_point(ax.scene, marker = :circle)

display(fig)

# Start/Stop Button
run = Button(fig[2,1]; label = "Start / Stop", tellwidth = false)
isrunning = Observable(false)
on(run.clicks) do clicks; isrunning[] = !isrunning[]; end
on(run.clicks) do clicks
    @async while isrunning[]
        isopen(fig.scene) || break
        
        # Zeitentwicklung beider DGLs.
        animstep!(IInner, PInner, 0.025)
        animstep!(IBorder, PBorder, 0.025)
        
        sleep(0.01)
    end
end 

# Wähle neue Anfangsbedingungen per Mausklick.
on(spoint) do z 
    x,y = z
    
    # Neue Anfangsbedingungen
    uin = get_init_inner(x,y,R,NI)
    ubor = get_init_border(x,y,R,NB)

    # Übergabe der Anfangsbedingungen an Integrator.
    reinit!(IInner, uin)
    reinit!(IBorder, ubor)
    
    # Observable Updaten.
    PInner[][:] = [Point2f(IInner[2*i-1], IInner[2*i]) for i in 1:NI]
    PBorder[][:] = [Point2f(IBorder[2*i-1], IBorder[2*i]) for i in 1:NB]
    
    # Observable auf Update aufmerksam machen
    notify(PInner)
    notify(PBorder)
end
